In [5]:
!pip install transformers accelerate peft ipywidgets --quiet

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 2.6 MB/s eta 0:00:0000:01m0:02m
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 9.5 MB/s eta 0:00:000:00:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 69.5 MB/s eta 0:00:00:00:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 52.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 2.6 MB/s eta 0:00:00:00:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 7.9 MB/s eta 0:00:00:00:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 30.5 MB/s eta 0:00:00:00:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 13.5 MB/s eta 0:00:0000:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 6.8 MB/s eta 0:00:00:00:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 18.5 MB/s eta 0:00:00:00:010:01


## Local Inference on GPU 
Model page: https://huggingface.co/Martico2432/mcollm1-2b

⚠️ If the generated code snippets do not work, please open an issue on either the [model repo](https://huggingface.co/Martico2432/mcollm1-2b)
			and/or on [huggingface.js](https://github.com/huggingface/huggingface.js/blob/main/packages/tasks/src/model-libraries-snippets.ts) 🙏

In [ ]:
import huggingface_hub
huggingface_hum.login()

In [6]:
import torch
from transformers import AutoModelForCausalLM, AutoTokenizer
from peft import PeftModel

# Base model repo for gemma-2b-it
base_model_name = "google/gemma-2b-it"

# Your LoRA adapter repo or local path
lora_adapter_path = "Martico2432/mcollm1-2b"

# Load tokenizer and base model
tokenizer = AutoTokenizer.from_pretrained(base_model_name)

# Load base model with half precision if CUDA available
device = "cuda" if torch.cuda.is_available() else "cpu"
base_model = AutoModelForCausalLM.from_pretrained(base_model_name, torch_dtype=torch.float16 if device=="cuda" else torch.float32)
base_model.to(device)

# Load LoRA adapter on top of base model
model = PeftModel.from_pretrained(base_model, lora_adapter_path)
model.to(device)
model.eval()

tokenizer_config.json:   0%|          | 0.00/34.2k [00:00<?, ?B/s]

tokenizer.model:   0%|          | 0.00/4.24M [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/17.5M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/636 [00:00<?, ?B/s]

`torch_dtype` is deprecated! Use `dtype` instead!


Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/137 [00:00<?, ?B/s]

PeftModelForCausalLM(
  (base_model): LoraModel(
    (model): GemmaForCausalLM(
      (model): GemmaModel(
        (embed_tokens): Embedding(256000, 2048, padding_idx=0)
        (layers): ModuleList(
          (0-17): 18 x GemmaDecoderLayer(
            (self_attn): GemmaAttention(
              (q_proj): lora.Linear(
                (base_layer): Linear(in_features=2048, out_features=2048, bias=False)
                (lora_dropout): ModuleDict(
                  (default): Dropout(p=0.05, inplace=False)
                )
                (lora_A): ModuleDict(
                  (default): Linear(in_features=2048, out_features=16, bias=False)
                )
                (lora_B): ModuleDict(
                  (default): Linear(in_features=16, out_features=2048, bias=False)
                )
                (lora_embedding_A): ParameterDict()
                (lora_embedding_B): ParameterDict()
                (lora_magnitude_vector): ModuleDict()
              )
              (k_pro

In [13]:
def generate_response(prompt, max_length=256, temperature=0.7):
    inputs = tokenizer(prompt, return_tensors="pt").to(device)
    with torch.no_grad():
        outputs = model.generate(
            **inputs,
            max_length=inputs['input_ids'].shape[-1] + max_length,
            temperature=temperature,
            do_sample=True,
            pad_token_id=tokenizer.eos_token_id,
            eos_token_id=tokenizer.eos_token_id,
        )
    # Slice off prompt tokens before decoding
    generated_tokens = outputs[0][inputs['input_ids'].shape[-1]:]
    response = tokenizer.decode(generated_tokens, skip_special_tokens=True)
    return response.strip()

In [14]:
import ipywidgets as widgets
from IPython.display import display, Markdown, clear_output

chat_history = []

input_box = widgets.Textarea(
    placeholder="Type your message here...",
    layout=widgets.Layout(width="100%", height="80px")
)
send_button = widgets.Button(description="Send", button_style="success")
output_area = widgets.Output(layout=widgets.Layout(border="1px solid black", padding="10px", height="400px", overflow_y="auto"))

def update_chat_display():
    with output_area:
        clear_output()
        for i, (user_msg, bot_msg) in enumerate(chat_history):
            display(Markdown(f"**🙋‍♂️ User:** {user_msg}"))
            display(Markdown(f"**🤖 Model:** {bot_msg}"))
            display(Markdown("---"))

def on_send_clicked(b):
    user_input = input_box.value.strip()
    if not user_input:
        return
    chat_history.append((user_input, "..."))
    update_chat_display()
    input_box.value = ""
    
    # Build prompt with conversation history for context
    prompt = ""
    for u, r in chat_history[:-1]:
        prompt += f"<start_of_turn>user\n{u}<end_of_turn>\n<start_of_turn>model\n{r}<end_of_turn>\n"
    prompt += f"<start_of_turn>user\n{user_input}<end_of_turn>\n<start_of_turn>model\n"
    
    response = generate_response(prompt)
    chat_history[-1] = (user_input, response)
    update_chat_display()

send_button.on_click(on_send_clicked)

display(input_box, send_button, output_area)

Textarea(value='', layout=Layout(height='80px', width='100%'), placeholder='Type your message here...')

Button(button_style='success', description='Send', style=ButtonStyle())

Output(layout=Layout(border_bottom='1px solid black', border_left='1px solid black', border_right='1px solid b…